In [1]:
import os
import numpy as np
from netCDF4 import Dataset
import xlwt
import pandas as pd
import xarray as xr
from metpy.interpolate import inverse_distance_to_grid
from functools import reduce
import sys
import maskout
import matplotlib.pyplot as plt
import cartopy.crs as ccrs
import matplotlib.ticker as mticker
from cartopy.mpl.ticker import LongitudeFormatter, LatitudeFormatter
from cartopy.mpl.gridliner import LONGITUDE_FORMATTER, LATITUDE_FORMATTER
import matplotlib as mpl
import cartopy.feature as cfeature
from netCDF4 import Dataset
from cartopy.util import add_cyclic_point
import matplotlib.colors as colors
import matplotlib.ticker as ticker
# %matplotlib widget
%config InlineBackend.figure_format = 'svg'

In [2]:
class MidpointNormalize(colors.Normalize): 
    def __init__(self, vmin=None, vmax=None, midpoint=None, clip=False):
        self.midpoint = midpoint
        super().__init__(vmin, vmax, clip)

    def __call__(self, value, clip=None):
        x, y = [self.vmin, self.midpoint, self.vmax], [0, 0.5, 1]
        return np.ma.masked_array(np.interp(value, x, y))

In [9]:
draw_what = np.load('E:\D1\diffusion\my_models\my_model_data/restored_image.npy')[0]

<>:1: SyntaxWarning: invalid escape sequence '\D'
<>:1: SyntaxWarning: invalid escape sequence '\D'
C:\Users\fired\AppData\Local\Temp\ipykernel_30212\3932874896.py:1: SyntaxWarning: invalid escape sequence '\D'
  draw_what = np.load('E:\D1\diffusion\my_models\my_model_data/restored_image.npy')[0]


In [3]:
draw_what = np.load('E:\D1\diffusion\my_models\my_model_data/20180203.npy')[0]

<>:1: SyntaxWarning: invalid escape sequence '\D'
<>:1: SyntaxWarning: invalid escape sequence '\D'
C:\Users\fired\AppData\Local\Temp\ipykernel_3420\3778835722.py:1: SyntaxWarning: invalid escape sequence '\D'
  draw_what = np.load('E:\D1\diffusion\my_models\my_model_data/20180203.npy')[0]


In [4]:
lon = np.linspace(70, 140, np.shape(draw_what)[1])
lat = np.linspace(60, 0, np.shape(draw_what)[0])
# # 画下面的彩色条子
min_of_draw_what = -1.0
max_of_draw_what = 1.0
spon_k = 0.6
# min_of_draw_what = round(float(np.nanmin(draw_what))*spon_k, 2)
# max_of_draw_what = round(float(np.nanmax(draw_what))*spon_k, 2)
lim = np.concatenate((np.linspace(min_of_draw_what,0,4),np.delete(np.linspace(0,max_of_draw_what,4), 0)),axis=0)
# 地图界限
with open("E:\D1/f01\data\CN-border-La.gmt") as src:
    context = src.read()
    blocks = [cnt for cnt in context.split('>') if len(cnt) > 0]
    borders = [np.fromstring(block, dtype=float, sep=' ') for block in blocks]

<>:11: SyntaxWarning: invalid escape sequence '\D'
<>:11: SyntaxWarning: invalid escape sequence '\D'
C:\Users\fired\AppData\Local\Temp\ipykernel_3420\3449646142.py:11: SyntaxWarning: invalid escape sequence '\D'
  with open("E:\D1/f01\data\CN-border-La.gmt") as src:


In [ ]:
fig = plt.figure(figsize=(6,6),facecolor='white')
myproj = ccrs.PlateCarree(central_longitude=0.0)#ccrs跟绘地图有关#调整图像中心位置
ax = fig.add_axes([0.10, 0.22, 0.8, 0.75],projection=myproj)#add_axes通过相对位置增加子图 
ax.add_feature(cfeature.LAND.with_scale('110m'))
for line in borders:
    ax.plot(line[0::2], line[1::2], '-', lw=0.5, color='k',
            transform=ccrs.Geodetic())
    
# Set figure extent设置图范围
ax.set_extent([70, 140, 10, 60])#摆正图像
# ax.set_xticks([70,80,90,100,110,120,130,140],crs=ccrs.PlateCarree())
# ax.set_yticks([10,20,30,40,50],crs=ccrs.PlateCarree())
ax.set_xticks(range(70,141,10),crs=ccrs.PlateCarree())
ax.set_yticks(range(10,61,10),crs=ccrs.PlateCarree())
lon_formatter = LongitudeFormatter(zero_direction_label=False)
lat_formatter = LatitudeFormatter()#定义一种坐标刻度样式为维度刻度	
ax.xaxis.set_major_formatter(lon_formatter)#改变X轴主刻度为经度样式
ax.yaxis.set_major_formatter(lat_formatter)
plt.tick_params(axis='both',labelsize=14)#刻度的字号
cmap1 = mpl.colors.ListedColormap(['#E11300', '#FF3100', '#FF9F00', '#FFBF3B', '#FFE877','#B3F0FA', '#95D2FA', '#77B8FA', '#4FA4F5', '#3B95F5'])#冷大
cmap1.set_over('darkred')
cmap1.set_under('navy')    #22就是最后一年，2016年
cf=plt.contourf(lon,lat,draw_what,levels=lim,cmap =cmap1,extend='both',zorder=0,transform=ccrs.PlateCarree(),norm=MidpointNormalize(midpoint=0))#画出等高线


colors =mpl.colors.ListedColormap(['black'])
# plt.title('precipitation anomaly', fontsize=14)
#plt.legend((),('A1',),loc='upper left',fontsize=20,ncol=2)
# plt.title('D2',fontsize=60,loc='left',y=0.85,x=0.02)#标题和标题大小
formatter = ticker.FormatStrFormatter('%.1f')
cbar=plt.colorbar(cf,cax=fig.add_axes([0.13, 0.20, 0.75, 0.03]),format=formatter, orientation='horizontal',cmap=cmap1)
cbar.ax.tick_params(labelsize=14)#条子的字号

clip=maskout.shp2clip(cf,ax, r"E:\D1\f01\data\province\china0.shp")
sub_ax = fig.add_axes([0.76, 0.29, 0.14, 0.155],projection=myproj)#小南海的位置
sub_ax.add_feature(cfeature.LAND.with_scale('110m'))
for line in borders:
    sub_ax.plot(line[0::2], line[1::2], '-', lw=0.5, color='k',
                transform=ccrs.Geodetic())
# Set figure extent设置图范围
sub_ax.set_extent([105, 125, 0, 25]) 
plt.subplots_adjust()
plt.text(.01, .99, '(d)', ha='left', va='top', transform=ax.transAxes, fontsize=14)
plt.show()